# 1. Rainfall Erosivity Factor Computation Using Kinetic Energy Equation

This code is developed to calculate rainfall erosivity factor (R factor) using kinetic energy equation based on **5-minute interval precipitation gauge data during 1994-2023** requested from Oklahoma Mesonet (chartman@mesonet.org). The data in the "RAIN" column is **cumulative rainfall amount with unit of inch**, which also includes **frozen precipitation** measured at the time of thaw. Each Mesonet observation contains a running accumulation of rainfall since either 6 PM CST or 7 PM CDT. As each new evening begins, the accumulated rainfall is reset to zero. The missing data are indicated by -99 or -999. More information can be seen https://mesonet.org/about/instruments.

The computation method 

## 1.1 Preparation

### 1.1.1 Save the rainfall data based on site ID (STID)
Since the raw data provided by Mesonet merge the data from different gauge sites, this code is to extract the rainfall data from unique site and save the data from one site in an file. The file name is the site ID.

In [30]:
import os
import pandas as pd
import glob

# Define the input directory for 5-minute rainfall data
path_5min_rainfall = os.path.join(os.getcwd(), "RAW")

# Define the output directory for saving storm data
path_each_station = os.path.join(os.getcwd(), "Each Station")

# Create the output directory if it doesn't exist
os.makedirs(path_each_station, exist_ok=True)

# Process each CSV file in the input directory
for file_path in glob.glob(os.path.join(path_5min_rainfall, '*.csv')):
    # Load the dataset
    df = pd.read_csv(file_path)

    # Extract unique station IDs
    unique_stations = df['STID'].unique()

    # Loop through each unique station, filter the DataFrame, and save to a new CSV
    for station in unique_stations:
        # Filter the DataFrame for the current station
        df_station = df[df['STID'] == station][['STID', 'TIME', 'RAIN']]

        # Define the output file path using the station name, safely handle file names
        output_file_name = f"{station.replace('/', '_')}.csv"  # Replace '/' with '_' to avoid path issues
        output_file_path = os.path.join(path_each_station, output_file_name)

        # Save the filtered DataFrame to a CSV file
        df_station.to_csv(output_file_path, index=False)
        print(f"Saved data for station {station} to {output_file_path}")

print("All files have been processed and saved.")


Saved data for station ACME to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\ACME.csv
Saved data for station ADAX to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\ADAX.csv
Saved data for station ALTU to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\ALTU.csv
Saved data for station ALV2 to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\ALV2.csv
Saved data for station ANT2 to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\ANT2.csv
Saved data for station APAC to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\APAC.csv
Saved data for station ARD2 to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\ARD2.csv
Saved data for station ARNE to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Each Station\A

KeyboardInterrupt: 

Check data format

In [ ]:
# Input
path_one_site =  os.path.join(os.getcwd(), "Each Station", "ACME.csv")

# Loat the dataset
df = pd.read_csv(path_one_site)

# Display first few rows
print(df.head())

# Display column names and data types
print(df.dtypes)


   STID              TIME  RAIN
0  ACME  1994-01-01T00:00   NaN
1  ACME  1994-01-01T00:05   NaN
2  ACME  1994-01-01T00:10   NaN
3  ACME  1994-01-01T00:15   NaN
4  ACME  1994-01-01T00:20   NaN
STID     object
TIME     object
RAIN    float64
dtype: object


### 1.1.2 Count the recording period for each site


In [7]:
import os
import pandas as pd

# Input and output directories
path_each_station = os.path.join(os.getcwd(), "Each Station")

path_result = os.path.join(os.getcwd(), "Result")
os.makedirs(path_result, exist_ok=True)

# Initialize an empty list to store station-wise data recording periods
station_periods = []

# Process each CSV file in the input directory
for filename in os.listdir(path_each_station):
    if filename.endswith('.csv'):
        filepath = os.path.join(path_each_station, filename)

        # Read the CSV file into a Pandas DataFrame
        df = pd.read_csv(filepath)

        # Convert the value in "TIME" column from string format to datetime objects
        df["TIME"] = pd.to_datetime(df["TIME"], format="%Y-%m-%dT%H:%M", errors='coerce')

        # Calculate the measurement period for the station
        start_time = df["TIME"].min()  # Earliest timestamp
        end_time = df["TIME"].max()    # Latest timestamp

        # Extract start and end years
        start_year = start_time.year if pd.notnull(start_time) else None
        end_year = end_time.year if pd.notnull(end_time) else None

        # Calculate the difference in years
        period_days = (end_time - start_time).days if pd.notnull(start_time) and pd.notnull(end_time) else 0
        period_years = period_days / 365.25  # Convert days to years

        # Append station and its period to the list
        station_periods.append({
            'STID': filename.split('.')[0], 
            'Start Year': start_year, 
            'End Year': end_year, 
            'Period Days': period_days,
            'Period Years': period_years
        })

# Convert the list of dictionaries to a DataFrame for recording periods
station_periods_df = pd.DataFrame(station_periods)

# Save the station periods DataFrame to a CSV file
output_file = os.path.join(path_result, 'station_periods.csv')
station_periods_df.to_csv(output_file, index=False)

# Print a success message and display the DataFrame for reference
print(f"Station periods have been saved to {output_file}.")
print(station_periods_df)


Station periods have been saved to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Result\station_periods.csv.
     STID  Start Year  End Year  Period Days  Period Years
0    ACME        1994      2024        10988     30.083504
1    ADAX        1994      2024        10988     30.083504
2    ALTU        1994      2024        10988     30.083504
3    ALV2        1998      2024         9177     25.125257
4    ANT2        2011      2024         4675     12.799452
..    ...         ...       ...          ...           ...
115  WILB        1994      2024        10988     30.083504
116  WIST        1994      2024        10988     30.083504
117  WOOD        1994      2024        10988     30.083504
118  WYNO        1994      2024        10988     30.083504
119  YUKO        2018      2024         2054      5.623546

[120 rows x 5 columns]


Count missing data for whole recording length

In [10]:
import os
import pandas as pd
import numpy as np

# Input and output directories
path_each_station = os.path.join(os.getcwd(), "Each Station")
path_result = os.path.join(os.getcwd(), "Result")
os.makedirs(path_result, exist_ok=True)

# List to store NaN count per file
nan_counts = []

# Process each CSV file in the input directory
for filename in os.listdir(path_each_station):
    if filename.endswith('.csv'):
        filepath = os.path.join(path_each_station, filename)

        # Read the CSV file into a Pandas DataFrame
        df = pd.read_csv(filepath)

        # Ensure "RAIN" column exists
        if "RAIN" in df.columns:
            # Replace only negative values in "RAIN" column with NaN
            df["RAIN"] = df["RAIN"].mask(df["RAIN"] < 0, np.nan)

            # Count total NaN values in the "RAIN" column
            total_nans = df["RAIN"].isna().sum()

            # Count total rows (time slots)
            total_timeslots = len(df)

            # Estimate percentage of NaN values
            nan_percentage = (total_nans / total_timeslots) * 100 if total_timeslots > 0 else 0

            # Store NaN count info
            nan_counts.append({
                'Filename': filename,
                'Total NaN Values in RAIN': total_nans,
                'Total Time Slots': total_timeslots,
                'NaN Percentage (%)': round(nan_percentage, 2)  # Rounded for clarity
            })

            # Save the modified DataFrame back to the same file
            df.to_csv(filepath, index=False)
            print(f"Updated negative values in 'RAIN' column to NaN in: {filename} | Total NaNs: {total_nans} | NaN %: {round(nan_percentage, 2)}%")

# Convert the list of NaN counts into a DataFrame
nan_counts_df = pd.DataFrame(nan_counts)

# Save the NaN counts summary to a CSV file
nan_count_file = os.path.join(path_result, 'nan_counts_summary_raw.csv')
nan_counts_df.to_csv(nan_count_file, index=False)

# Print success message and display the summary
print(f"NaN count summary has been saved to {nan_count_file}.")
print(nan_counts_df)


Updated negative values in 'RAIN' column to NaN in: ACME.csv | Total NaNs: 38957 | NaN %: 1.23%
Updated negative values in 'RAIN' column to NaN in: ADAX.csv | Total NaNs: 35664 | NaN %: 1.13%
Updated negative values in 'RAIN' column to NaN in: ALTU.csv | Total NaNs: 58820 | NaN %: 1.86%
Updated negative values in 'RAIN' column to NaN in: ALV2.csv | Total NaNs: 51184 | NaN %: 1.94%
Updated negative values in 'RAIN' column to NaN in: ANT2.csv | Total NaNs: 694 | NaN %: 0.05%
Updated negative values in 'RAIN' column to NaN in: APAC.csv | Total NaNs: 182260 | NaN %: 5.76%
Updated negative values in 'RAIN' column to NaN in: ARD2.csv | Total NaNs: 3893 | NaN %: 0.19%
Updated negative values in 'RAIN' column to NaN in: ARNE.csv | Total NaNs: 6120 | NaN %: 0.19%
Updated negative values in 'RAIN' column to NaN in: BBOW.csv | Total NaNs: 25475 | NaN %: 2.98%
Updated negative values in 'RAIN' column to NaN in: BEAV.csv | Total NaNs: 18560 | NaN %: 0.59%
Updated negative values in 'RAIN' column to

### 1.

In [12]:
# Import required libraries
import os
import pandas as pd

# Input and output directories
path_each_station = os.path.join(os.getcwd(), "Each Station")
path_filtered = os.path.join(os.getcwd(), "Site_1995-2023")  # Output folder
os.makedirs(path_filtered, exist_ok=True)

# Define the required date range
start_date = pd.Timestamp("1995-01-01")   
end_date = pd.Timestamp("2023-12-31")

# Process each CSV file in the input directory
for filename in os.listdir(path_each_station):
    if filename.endswith('.csv'):
        filepath = os.path.join(path_each_station, filename)

        # Read the CSV file into a Pandas DataFrame
        df = pd.read_csv(filepath)

        # Convert the value in "TIME" column from string format to datetime objects
        df["TIME"] = pd.to_datetime(df["TIME"], format="%Y-%m-%dT%H:%M", errors='coerce')

        # Filter out rows with invalid or missing dates
        df = df.dropna(subset=["TIME"])

        # Filter the data to include only rows within the specified date range
        df_filtered = df[(df["TIME"] >= start_date) & (df["TIME"] <= end_date)]

        # Check if the filtered data covers the required date range
        if not df_filtered.empty and df_filtered["TIME"].min() <= start_date and df_filtered["TIME"].max() >= end_date:
            new_file_path = os.path.join(path_filtered, filename)
            df_filtered.to_csv(new_file_path, index=False)
            print(f"Saved file with required date range: {filename}")


Saved file with required date range: ACME.csv
Saved file with required date range: ADAX.csv
Saved file with required date range: ALTU.csv
Saved file with required date range: APAC.csv
Saved file with required date range: ARNE.csv
Saved file with required date range: BEAV.csv
Saved file with required date range: BESS.csv
Saved file with required date range: BIXB.csv
Saved file with required date range: BLAC.csv
Saved file with required date range: BOIS.csv
Saved file with required date range: BREC.csv
Saved file with required date range: BRIS.csv
Saved file with required date range: BUFF.csv
Saved file with required date range: BURB.csv
Saved file with required date range: BURN.csv
Saved file with required date range: BUTL.csv
Saved file with required date range: BYAR.csv
Saved file with required date range: CAMA.csv
Saved file with required date range: CENT.csv
Saved file with required date range: CHAN.csv
Saved file with required date range: CHER.csv
Saved file with required date rang

In [17]:
# Import required libraries
import os
import pandas as pd
import numpy as np

# Input 
path_each_station = os.path.join(os.getcwd(), "Site_1995-2023")
os.makedirs(path_each_station, exist_ok=True)

# Output
path_result = os.path.join(os.getcwd(), "Result")
os.makedirs(path_result, exist_ok=True)

# List to store NaN count per file
nan_counts = []

# Process each CSV file in the input directory
for filename in os.listdir(path_each_station):
    if filename.endswith('.csv'):
        filepath = os.path.join(path_each_station, filename)

        # Read the CSV file into a Pandas DataFrame
        df = pd.read_csv(filepath)

        # Ensure "RAIN" column exists
        if "RAIN" in df.columns:
           
            # Count total NaN values in the "RAIN" column
            total_nans = df["RAIN"].isna().sum()

            # Count total rows (time slots)
            total_timeslots = len(df)

            # Estimate percentage of NaN values
            nan_percentage = (total_nans / total_timeslots) * 100 if total_timeslots > 0 else 0

            # Store NaN count info
            nan_counts.append({
                'Filename': filename,
                'Total NaN Values in RAIN': total_nans,
                'Total Time Slots': total_timeslots,
                'NaN Percentage (%)': round(nan_percentage, 2)  # Rounded for clarity
            })

            # Save the modified DataFrame back to the same file
            df.to_csv(filepath, index=False)
            print(f"Updated NaN in 'RAIN' column for: {filename} | Total NaNs: {total_nans} | NaN %: {round(nan_percentage, 2)}%")

# Convert the list of NaN counts into a DataFrame
nan_counts_df = pd.DataFrame(nan_counts)

# Save the NaN counts summary to a CSV file
nan_count_file = os.path.join(path_result, 'nan_counts_summary_1995-2023.csv')
nan_counts_df.to_csv(nan_count_file, index=False)

# Print success message and display the summary
print(f"NaN count summary has been saved to {nan_count_file}.")
print(nan_counts_df)

Updated NaN in 'RAIN' column for: ACME.csv | Total NaNs: 25124 | NaN %: 0.82%
Updated NaN in 'RAIN' column for: ADAX.csv | Total NaNs: 35643 | NaN %: 1.17%
Updated NaN in 'RAIN' column for: ALTU.csv | Total NaNs: 58719 | NaN %: 1.93%
Updated NaN in 'RAIN' column for: APAC.csv | Total NaNs: 172717 | NaN %: 5.66%
Updated NaN in 'RAIN' column for: ARNE.csv | Total NaNs: 6118 | NaN %: 0.2%
Updated NaN in 'RAIN' column for: BEAV.csv | Total NaNs: 18552 | NaN %: 0.61%
Updated NaN in 'RAIN' column for: BESS.csv | Total NaNs: 21729 | NaN %: 0.71%
Updated NaN in 'RAIN' column for: BIXB.csv | Total NaNs: 11004 | NaN %: 0.36%
Updated NaN in 'RAIN' column for: BLAC.csv | Total NaNs: 24419 | NaN %: 0.8%
Updated NaN in 'RAIN' column for: BOIS.csv | Total NaNs: 13685 | NaN %: 0.45%
Updated NaN in 'RAIN' column for: BREC.csv | Total NaNs: 25484 | NaN %: 0.84%
Updated NaN in 'RAIN' column for: BRIS.csv | Total NaNs: 130753 | NaN %: 4.29%
Updated NaN in 'RAIN' column for: BUFF.csv | Total NaNs: 10843 | 

#### Remove missing data 
Remove the sites with percentage of missing data(NaN values) > 5%. Remove the NaN values in the rainfall data from rest of the sites, and extract the sites with recording started from 1995-01-01 to 2023-12-31.

In [33]:
import os
import pandas as pd

# Input directory
path_each_station = os.path.join(os.getcwd(), "Site_1995-2023")

# Output directories
path_cleaned = os.path.join(os.getcwd(), "Cleaned_Site_1995-2023")  # Folder for cleaned files
os.makedirs(path_cleaned, exist_ok=True)

path_result = os.path.join(os.getcwd(), "Result")  # Folder to save missing data statistics
os.makedirs(path_result, exist_ok=True)

# Define the required date range
start_date = pd.Timestamp("1995-01-01")
end_date = pd.Timestamp("2023-12-31")

# Initialize a list to store missing data statistics
nan_counts = []

# Process each CSV file in the input directory
for filename in os.listdir(path_each_station):
    if filename.endswith('.csv'):
        filepath = os.path.join(path_each_station, filename)

        # Read the CSV file into a Pandas DataFrame
        df = pd.read_csv(filepath)

        # Convert "TIME" column to datetime
        if "TIME" in df.columns and "RAIN" in df.columns:
            df["TIME"] = pd.to_datetime(df["TIME"], errors='coerce')  # Convert TIME to datetime

            # Count total NaN values in the "RAIN" column
            total_nans = df["RAIN"].isna().sum()

            # Count total rows (time slots)
            total_timeslots = len(df)

            # Estimate percentage of NaN values
            nan_percentage = (total_nans / total_timeslots) * 100 if total_timeslots > 0 else 0

            # Store missing data statistics
            nan_counts.append({
                "Site": filename,
                "Total_Missing": total_nans,
                "Total_Records": total_timeslots,
                "Missing_Percentage": round(nan_percentage, 2)
            })

            # Skip site if missing percentage > 5%
            if nan_percentage > 5:
                print(f"❌ Skipping {filename} (Missing data > 5%: {round(nan_percentage, 2)}%)")
                continue  # Do not process or save this file

            # Remove rows with missing (NaN) values in "RAIN" only
            df_cleaned = df.dropna(subset=["RAIN"])

            # Filter data within the required date range
            df_filtered = df_cleaned[(df_cleaned["TIME"] >= start_date) & (df_cleaned["TIME"] <= end_date)]

            # Ensure the cleaned file still covers the full period
            if not df_filtered.empty and df_filtered["TIME"].min() <= start_date and df_filtered["TIME"].max() >= end_date:
                # Save the cleaned and filtered DataFrame
                cleaned_filepath = os.path.join(path_cleaned, filename)
                df_filtered.to_csv(cleaned_filepath, index=False)
                print(f"✅ Saved {filename} | Original: {total_timeslots} | Cleaned: {len(df_cleaned)} | Filtered: {len(df_filtered)}")
            else:
                print(f"❌ Skipping {filename} (Does not fully cover 1995-2023 after removing NaN values)")

# Convert missing data statistics to DataFrame and save it
missing_data_df = pd.DataFrame(nan_counts)
missing_data_filepath = os.path.join(path_result, "nan_counts_1995-2023_less then 5%.csv")
missing_data_df.to_csv(missing_data_filepath, index=False)

print("\nProcessing completed. Valid cleaned files are saved in 'Cleaned_Site_1995-2023' folder.")
print(f"Missing data statistics saved in {missing_data_filepath}")


✅ Saved ACME.csv | Original: 3050209 | Cleaned: 3025085 | Filtered: 3025085
✅ Saved ADAX.csv | Original: 3050209 | Cleaned: 3014566 | Filtered: 3014566
✅ Saved ALTU.csv | Original: 3050209 | Cleaned: 2991490 | Filtered: 2991490
❌ Skipping APAC.csv (Missing data > 5%: 5.66%)
✅ Saved ARNE.csv | Original: 3050209 | Cleaned: 3044091 | Filtered: 3044091
✅ Saved BEAV.csv | Original: 3050209 | Cleaned: 3031657 | Filtered: 3031657
✅ Saved BESS.csv | Original: 3050209 | Cleaned: 3028480 | Filtered: 3028480
✅ Saved BIXB.csv | Original: 3050209 | Cleaned: 3039205 | Filtered: 3039205
✅ Saved BLAC.csv | Original: 3050209 | Cleaned: 3025790 | Filtered: 3025790
✅ Saved BOIS.csv | Original: 3050209 | Cleaned: 3036524 | Filtered: 3036524
✅ Saved BREC.csv | Original: 3050209 | Cleaned: 3024725 | Filtered: 3024725
✅ Saved BRIS.csv | Original: 3050209 | Cleaned: 2919456 | Filtered: 2919456
✅ Saved BUFF.csv | Original: 3050209 | Cleaned: 3039366 | Filtered: 3039366
✅ Saved BURB.csv | Original: 3050209 | Cl

### 1.1.3 Storm identification

Each Mesonet observation records a running accumulation of rainfall starting from either 6 PM CST or 7 PM CDT. At the beginning of each new evening, the accumulated rainfall resets to zero.

This code identifies the start of a storm based on the accumulated rainfall depth, tracking it until the accumulation resets to zero.

In [4]:
import os
import glob
import pandas as pd

# Define input and output directories
path_long_term = os.path.join(os.getcwd(), "Cleaned_Site_1995-2023")
path_Storms_Identified_By_Increas = os.path.join(os.getcwd(), "Storms_Identified_By_Increas_29")

# Create the output directory if it doesn't exist
os.makedirs(path_Storms_Identified_By_Increas, exist_ok=True)

# Search for CSV files in the input directory
pattern = os.path.join(path_long_term, '**/*.csv')
csv_files = glob.glob(pattern, recursive=True)

# Process each CSV file
for file_path in csv_files:
    df = pd.read_csv(file_path)

    # Initialize a storm marker column
    df['Storm_Marker'] = False

    # Mark rows where RAIN increases from the previous value
    for i in range(1, len(df)):
        if df.loc[i, 'RAIN'] > df.loc[i - 1, 'RAIN']:
            df.loc[i, 'Storm_Marker'] = True
            df.loc[i - 1, 'Storm_Marker'] = True  # Mark the starting point

    # Filter the DataFrame to keep only rows marked as part of a storm
    storm_df = df[df['Storm_Marker']].copy()  # Work on a copy to avoid warnings

    # Check if there are any storms identified
    if not storm_df.empty:
        # Define the new file path in the output directory
        relative_path = os.path.relpath(file_path, path_long_term)
        new_file_path = os.path.join(path_Storms_Identified_By_Increas, relative_path)

        # Create subdirectories in the output directory if they don't exist
        os.makedirs(os.path.dirname(new_file_path), exist_ok=True)

        # Save the storm data to a new CSV file
        storm_df.drop('Storm_Marker', axis=1, inplace=True)  # Remove the marker column
        storm_df.to_csv(new_file_path, index=False)

        print(f"Storm data saved for {os.path.basename(file_path)} to {new_file_path}")
    else:
        print(f"No storm identified in {os.path.basename(file_path)}.")

Storm data saved for ACME.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Identified_By_Increas_29\ACME.csv
Storm data saved for ADAX.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Identified_By_Increas_29\ADAX.csv
Storm data saved for ALTU.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Identified_By_Increas_29\ALTU.csv
Storm data saved for ARNE.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Identified_By_Increas_29\ARNE.csv
Storm data saved for BEAV.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Identified_By_Increas_29\BEAV.csv
Storm data saved for BESS.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Identified_By_Increas_29\BESS.csv
Storm data saved for BIXB.csv to e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storms_Ident

Calcualte rainfall depth and rainfall intensity in each recording interval.

In [ ]:
import pandas as pd
import os

# Define input and output paths
path_input = os.path.join(os.getcwd(), "Storms_Identified_By_Increas_29")
path_output = os.path.join(os.getcwd(), "Storm interval information")
os.makedirs(path_output, exist_ok=True)

# Process each file in the input directory
for file_name in os.listdir(path_input):
    if file_name.endswith(".csv"):  # Ensure the file is a CSV
        file_path = os.path.join(path_input, file_name)
        
        # Load the file
        data = pd.read_csv(file_path)
        
        # Rename column "RAIN" to "Cumulative rain depth (inch)"
        data.rename(columns={"RAIN": "Cumulative rain depth (inch)"}, inplace=True)
        
        # Convert inches to millimeters and save results in a new column
        data["Cumulative rain depth (mm)"] = data["Cumulative rain depth (inch)"] * 25.4
        
        # Calculate time intervals in minutes
        
        # pd.to_datetime(data["TIME"])  # Ensure TIME is in datetime format
        data["Duration of interval (min)"] = pd.to_datetime(data["TIME"]).diff().dt.total_seconds().div(60).fillna(0)
        
        # Calculate rainfall depth in each interval
        data["Rain depth in interval (inch)"] = data["Cumulative rain depth (inch)"].diff().fillna(0)
        data["Rain depth in interval (mm)"] = data["Rain depth in interval (inch)"] * 25.4

        # Calculate intensity
        data["Rainfall intensity (inch/hr)"] = data["Rain depth in interval (inch)"] / (data["Duration of interval (min)"] / 60)
        data["Rainfall intensity (mm/hr)"] = data["Rain depth in interval (mm)"] / (data["Duration of interval (min)"] / 60)
        
        # Save the processed data
        output_file = os.path.join(path_output, f"{file_name}")
        data.to_csv(output_file, index=False)
        
        print(f"Processed and saved: {output_file}")

print("All files have been processed and saved.")


Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\ACME.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\ADAX.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\ALTU.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\ARNE.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\BEAV.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\BESS.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Storm interval information\BIXB.csv
Processed and saved: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computat

Check data 

In [ ]:
path_input = os.path.join(os.getcwd(), "Storm interval information","ACME.csv")

# Loat the dataset
df = pd.read_csv(path_input)

# Display first few rows
print(df.head())

# Display column names and data types
print(df.dtypes)

   STID                 TIME  Cumulative rain depth (inch)  \
0  ACME  1995-01-05 21:50:00                          0.00   
1  ACME  1995-01-05 21:55:00                          0.01   
2  ACME  1995-01-05 22:05:00                          0.01   
3  ACME  1995-01-05 22:10:00                          0.02   
4  ACME  1995-01-06 06:00:00                          0.00   

   Cumulative rain depth (mm)  Duration of interval (min)  \
0                       0.000                         0.0   
1                       0.254                         5.0   
2                       0.254                        10.0   
3                       0.508                         5.0   
4                       0.000                       470.0   

   Rain depth in interval (inch)  Rain depth in interval (mm)  \
0                           0.00                        0.000   
1                           0.01                        0.254   
2                           0.00                        0.000   


### 1.1.4 Storm Separation
This code consider that a 5-minute interval with a rainfall depth of zero that no rainfall event occurred. This code checks each row of the DataFrame to see if there is '5-min Rainfall (mm)' > 0. Encounting 5-min Rainfall is not > 0 (no rainfall events), the current storm is determined and it increments the storm_counter, repeating the process for the next storm.


In [ ]:
import os
import glob
import pandas as pd

# Define input directory
path_Storms_Identified_By_Increas = os.path.join(os.getcwd(), "Storm interval information")

# Find all CSV files in the input directory
pattern = os.path.join(path_Storms_Identified_By_Increas, '*.csv')
csv_files = glob.glob(pattern)

# Define output directory
path_single_storm = os.path.join(os.getcwd(), "Single_Storm_29")
os.makedirs(path_single_storm, exist_ok=True)  # Ensure output directory exists

def reset_first_row_columns_to_zero(df, columns):
    """
    Reset specified columns in the first row of the DataFrame to 0.
    """
    for column in columns:
        if column in df.columns:
            df.iloc[0, df.columns.get_loc(column)] = 0
    return df

def process_and_save_rainfall_events(df, path_single_storm, station_id):
    """
    Identify and save storm events. Only the first row of specified columns is reset to 0.
    """
    event_number = 0
    storm_start_index = None
    in_storm = False

    # Specify columns to reset to 0 in the first row
    columns_to_reset = [
        "Cumulative rain depth (inch)", 
        "Cumulative rain depth (mm)", 
        "Duration of interval (min)", 
        "Rain depth in interval (inch)", 
        "Rain depth in interval (mm)",
        "Rainfall intensity (inch/hr)",
        "Rainfall intensity (mm/hr)"
    ]

    for i in range(len(df) - 1):
        current_rain = df.loc[i, 'Cumulative rain depth (inch)']
        next_rain = df.loc[i + 1, 'Cumulative rain depth (inch)']

        # Start a new storm
        if current_rain == 0 and next_rain > 0 and not in_storm:
            storm_start_index = i
            in_storm = True

        # End the current storm
        elif in_storm and (next_rain < current_rain or next_rain == 0):
            event_number += 1
            event_df = df.loc[storm_start_index:i].copy()  # Extract storm data

            # Reset specified columns to 0 in the first row
            event_df = reset_first_row_columns_to_zero(event_df, columns_to_reset)

            # Define event-specific file name and save path
            event_filename = f"{station_id}_event_{event_number}.csv"
            save_path = os.path.join(path_single_storm, f"{station_id}", event_filename)
            os.makedirs(os.path.dirname(save_path), exist_ok=True)  # Ensure station folder exists

            # Save the processed event data
            event_df.to_csv(save_path, index=False)
            in_storm = False
            storm_start_index = i + 1 if next_rain == 0 else None

    # Handle cases where the dataset ends while still in a storm
    if in_storm:
        event_number += 1
        event_df = df.loc[storm_start_index:len(df) - 1].copy()

        # Reset specified columns to 0 in the first row
        event_df = reset_first_row_columns_to_zero(event_df, columns_to_reset)

        event_filename = f"{station_id}_event_{event_number}.csv"
        save_path = os.path.join(path_single_storm, f"{station_id}", event_filename)
        os.makedirs(os.path.dirname(save_path), exist_ok=True)
        event_df.to_csv(save_path, index=False)

    return {"station_id": station_id, "events_saved": event_number}

# Process each file
for file_path in csv_files:
    df = pd.read_csv(file_path)

    # Extract station ID assuming 'STID' column exists
    if 'STID' in df.columns:
        station_id = df.iloc[0]['STID']
    else:
        raise KeyError(f"The file {file_path} does not contain 'STID' column.")

    # Process and save storm events
    process_and_save_rainfall_events(df, path_single_storm, station_id)

print("DONE!")


Processing complete: Storm events extracted and first-row columns reset to 0.


check data

In [ ]:
path_input = os.path.join(os.getcwd(), "Single_Storm_29","ACME","ACME_event_1.csv")

# Loat the dataset
df = pd.read_csv(path_input)

# Display first few rows
print(df.head())

# Display column names and data types
print(df.dtypes)

### 1.1.5 Investigate Rainfall Intensity 
This code is to conduct statistics of intensity for each site and for whole state of Oklahoma. 

In [34]:
import os
import glob
import pandas as pd

# Input directory
path_single_storm = os.path.join(os.getcwd(), "Single_Storm_29")
pattern = os.path.join(path_single_storm, '**/*.csv')
csv_files = glob.glob(pattern, recursive=True)

# Output directory
path_result = os.path.join(os.getcwd(), "Result")
os.makedirs(path_result, exist_ok=True)

# Initialize lists to store statistics
site_statistics = []
all_data_inch = []  # List to store all rainfall intensity values in inch/hr across sites
all_data_mm = []    # List to store all rainfall intensity values in mm/hr across sites

# Process each CSV file
for file in csv_files:
    try:
        # Read the CSV file
        df = pd.read_csv(file)

        # Check if the relevant columns exist
        has_inch = "Rainfall intensity (inch/hr)" in df.columns
        has_mm = "Rainfall intensity (mm/hr)" in df.columns

        # Skip files without any valid rainfall intensity column
        if not has_inch and not has_mm:
            print(f"⚠️ Skipping {file}: No valid rainfall intensity column found.")
            continue

        # Extract site name from the file name
        site_name = os.path.basename(file).split('.')[0]

        # Prepare statistics dictionary for the site
        stats = {"Site": site_name}

        # Process rainfall intensity (inch/hr)
        if has_inch:
            rainfall_data_inch = df["Rainfall intensity (inch/hr)"].dropna().tolist()
            all_data_inch.extend(rainfall_data_inch)

            stats.update({
                "Mean_Intensity (inch/hr)": pd.Series(rainfall_data_inch).mean(),
                "Median_Intensity (inch/hr)": pd.Series(rainfall_data_inch).median(),
                "Max_Intensity (inch/hr)": pd.Series(rainfall_data_inch).max(),
                "Min_Intensity (inch/hr)": pd.Series(rainfall_data_inch).min(),
                "Std_Dev (inch/hr)": pd.Series(rainfall_data_inch).std()
            })

        # Process rainfall intensity (mm/hr)
        if has_mm:
            rainfall_data_mm = df["Rainfall intensity (mm/hr)"].dropna().tolist()
            all_data_mm.extend(rainfall_data_mm)

            stats.update({
                "Mean_Intensity (mm/hr)": pd.Series(rainfall_data_mm).mean(),
                "Median_Intensity (mm/hr)": pd.Series(rainfall_data_mm).median(),
                "Max_Intensity (mm/hr)": pd.Series(rainfall_data_mm).max(),
                "Min_Intensity (mm/hr)": pd.Series(rainfall_data_mm).min(),
                "Std_Dev (mm/hr)": pd.Series(rainfall_data_mm).std()
            })

        # Append statistics for the site
        site_statistics.append(stats)

    except Exception as e:
        print(f"❌ Error processing {file}: {e}")

# Convert site-specific statistics to DataFrame
site_stats_df = pd.DataFrame(site_statistics)

# Save site-specific statistics to a CSV file
output_file_sites = os.path.join(path_result, "rainfall_intensity_statistics_by_site.csv")
site_stats_df.to_csv(output_file_sites, index=False)

# Compute overall statistics across all sites
overall_stats = {}

if all_data_inch:
    overall_stats.update({
        "Mean_Intensity (inch/hr)": pd.Series(all_data_inch).mean(),
        "Median_Intensity (inch/hr)": pd.Series(all_data_inch).median(),
        "Max_Intensity (inch/hr)": pd.Series(all_data_inch).max(),
        "Min_Intensity (inch/hr)": pd.Series(all_data_inch).min(),
        "Std_Dev (inch/hr)": pd.Series(all_data_inch).std()
    })

if all_data_mm:
    overall_stats.update({
        "Mean_Intensity (mm/hr)": pd.Series(all_data_mm).mean(),
        "Median_Intensity (mm/hr)": pd.Series(all_data_mm).median(),
        "Max_Intensity (mm/hr)": pd.Series(all_data_mm).max(),
        "Min_Intensity (mm/hr)": pd.Series(all_data_mm).min(),
        "Std_Dev (mm/hr)": pd.Series(all_data_mm).std()
    })

# Convert overall statistics to DataFrame
overall_stats_df = pd.DataFrame([overall_stats])

# Save overall statistics to a CSV file
output_file_overall = os.path.join(path_result, "rainfall_intensity_statistics_all_sites.csv")
overall_stats_df.to_csv(output_file_overall, index=False)

# Print completion message
print(f"✅ Statistics for each site saved to: {output_file_sites}")
print(f"✅ Overall statistics across all sites saved to: {output_file_overall}")


✅ Statistics for each site saved to: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Result\rainfall_intensity_statistics_by_site.csv
✅ Overall statistics across all sites saved to: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Result\rainfall_intensity_statistics_all_sites.csv


check data


In [ ]:
path_input = os.path.join(os.getcwd(), "Result","rainfall_intensity_statistics_by_site.csv")

# Loat the dataset
df = pd.read_csv(path_input)

# Display first few rows
print(df.head())

# Display column names and data types
print(df.dtypes)

In [ ]:
path_input = os.path.join(os.getcwd(), "Result","rainfall_intensity_statistics_all_sites.csv")

# Loat the dataset
df = pd.read_csv(path_input)

# Display first few rows
print(df.head())

# Display column names and data types
print(df.dtypes)

## 1.2 Select Effective Storms
Before identify the effective storms, this code calculates the accumulated rainfall (head named as 'Cumulative RAIN (mm)') for each storm by alculating the cumulative sum of the 5-minute interval rainfall depth ('5-min Rainfall (mm)').
An effective storm is defined as a rainfall event that has little effect on water erosion since it has a low amount and intensity. In this section, the storm events with the Cumulative RAIN < 0.5 inches (12.5 mm) are deleted (AH ARS, 2013).

In [36]:
import os
import glob
import pandas as pd

# Define input 
path_single_storm = os.path.join(os.getcwd(), "Single_Storm_29")
pattern = os.path.join(path_single_storm, '**/*.csv')
csv_files = glob.glob(pattern, recursive=True)

# Define output
path_effective_storm = os.path.join(os.getcwd(), "Effective_Storms_29")
os.makedirs(path_effective_storm, exist_ok=True)

# Dictionary to count storm events per station
storm_event_counters = {}

# Process each CSV file
for file_path in csv_files:
    df = pd.read_csv(file_path)

    # Check if cumulative rainfall exceeds 0.5 inch (12.7 mm) at any point
    if df['Cumulative rain depth (inch)'].max() < 0.5:
        continue  # Skip if cumulative rainfall never exceeds 0.5 inch (12.7 mm)

    # Determine station ID (use 'STID' if available, else use directory name)
    station_id = df['STID'].iloc[0] if 'STID' in df.columns else os.path.basename(os.path.dirname(file_path))

    # Create output directory for the station if it doesn't exist
    output_dir_station = os.path.join(path_effective_storm, station_id)
    if not os.path.exists(output_dir_station):
        os.makedirs(output_dir_station)

    # Increment the storm event counter for the current station
    storm_event_counters[station_id] = storm_event_counters.get(station_id, 0) + 1

    # Construct the new file name with the updated index
    new_file_name = f"{station_id}_event_{storm_event_counters[station_id]}.csv"
    new_file_path = os.path.join(output_dir_station, new_file_name)

    # Save the filtered DataFrame to a new CSV file
    df.to_csv(new_file_path, index=False)


check data

In [56]:
path_input = os.path.join(os.getcwd(), "Effective_Storms_29", "ACME","ACME_event_1.csv")

# Loat the dataset
df = pd.read_csv(path_input)

# Display first few rows
print(df.head())

# Display column names and data types
print(df.dtypes)

   STID                 TIME  Cumulative rain depth (inch)  \
0  ACME  2007-04-17 18:25:00                          0.00   
1  ACME  2007-04-17 18:30:00                          0.01   
2  ACME  2007-04-17 18:35:00                          0.02   
3  ACME  2007-04-17 18:40:00                          0.03   
4  ACME  2007-04-17 18:45:00                          0.04   

   Cumulative rain depth (mm)  Duration of interval (min)  \
0                       0.000                         0.0   
1                       0.254                         5.0   
2                       0.508                         5.0   
3                       0.762                         5.0   
4                       1.016                         5.0   

   Rain depth in interval (inch)  Rain depth in interval (mm)  \
0                           0.00                        0.000   
1                           0.01                        0.254   
2                           0.01                        0.254   


## 1.3 Calculation 

### 1.3.1 Calculate Intensity and Kinetic Energy 
This section is to
1) calculate rainfall intensity for each 5-minute interval, which is an input in kinetic energy equation.
2) find the maximum 30-minute intensity, also known as the maximum precipitation amount within 30 minutes.

In [43]:
import os
import glob
import pandas as pd
import numpy as np

# Input directory
path_effective_storm = os.path.join(os.getcwd(), "Effective_Storms_29")
pattern = os.path.join(path_effective_storm, '**/*.csv')  # Pattern to match all CSV files
csv_files = glob.glob(pattern, recursive=True)  # Find all files matching the pattern

# Output directory
path_rainfall_intensity = os.path.join(os.getcwd(), "Rainfall_intensity_29")
os.makedirs(path_rainfall_intensity, exist_ok=True)

# Function to calculate rainfall intensity and related metrics
def calculate_rainfall_intensity(df):
    # Compute unit energy (MJ/ha*mm)
    df['Unit energy (MJ/ha*mm)'] = 0.29 * (1 - 0.72 * np.exp(-0.082 * df['Rainfall intensity (mm/hr)']))

    # Compute energy in the interval (MJ/ha)
    df['Energy in Interval (MJ/ha)'] = df['Unit energy (MJ/ha*mm)'] * df['Rain depth in interval (mm)'].astype(float)

    # Add 5-minute rainfall (from interval)
    df['5-Min Rainfall (mm)'] = df['Rain depth in interval (mm)'].fillna(0)

    # Compute rolling sums for 10, 15, 20, 25, 30-minute rainfall
    for interval in [10, 15, 20, 25, 30]:
        column_name = f'{interval}-Min Rainfall (mm)'
        df[column_name] = df['5-Min Rainfall (mm)'].rolling(window=interval // 5, min_periods=1).sum()

        # Fill first rows with 0 where the rolling window is incomplete
        df.loc[0:interval // 5 - 1, column_name] = 0

    return df

# Process each CSV file
for file_path in csv_files:
    # Read the input file
    df = pd.read_csv(file_path)

    # Calculate rainfall intensity and related metrics
    df = calculate_rainfall_intensity(df)

    # Extract station ID from the first row
    station_id = df['STID'].iloc[0]

    # Create a subfolder for the station
    subfolder_path = os.path.join(path_rainfall_intensity, station_id)
    os.makedirs(subfolder_path, exist_ok=True)

    # Define the output file path in the station's subfolder
    new_file_path = os.path.join(subfolder_path, os.path.basename(file_path))

    # Save the processed DataFrame to a new CSV file
    df.to_csv(new_file_path, index=False)
    
print('All files processed successfully!')


File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_intensity_29\ACME\ACME_event_1.csv
File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_intensity_29\ACME\ACME_event_10.csv
File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_intensity_29\ACME\ACME_event_100.csv
File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_intensity_29\ACME\ACME_event_101.csv
File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_intensity_29\ACME\ACME_event_102.csv
File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_intensity_29\ACME\ACME_event_103.csv
File saved for station ACME: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Rainfall_inte

### 1.3.2 Calculate rainfall erosivity 

In [45]:
# Input and output directories
path_rainfall_intensity = os.path.join(os.getcwd(), "Rainfall_intensity_29")  # input 
path_rainfall_erosivity = os.path.join(os.getcwd(), "Rainfall_erosivity_29")  # output
os.makedirs(path_rainfall_erosivity, exist_ok=True)

# Find all the CSV files recursively in the input directory
csv_files = glob.glob(os.path.join(path_rainfall_intensity, '**/*.csv'), recursive=True)

# Function to extract station ID from the first 4 characters of the file name
def extract_station_id(file_name):
    return os.path.basename(file_name)[:4]

# List to collect summary data for all storms across all stations
summary_data = []

# Process each CSV file
for file_path in csv_files:
    df = pd.read_csv(file_path)

    # Extract components and create new columns
    df['TIME'] = pd.to_datetime(df['TIME'], format="%Y-%m-%d %H:%M:%S", errors='coerce')
    df['Month'] = df['TIME'].dt.month
    df['Day'] = df['TIME'].dt.day
    df['Year'] = df['TIME'].dt.year
    df['Hour'] = df['TIME'].dt.hour
    df['Minute'] = df['TIME'].dt.minute

    Total_rainfall_mm = df['Cumulative rain depth (mm)'].max()
    Time = df['TIME']

    # If the duration of a storm is less than 30 min, the I_30 is twice the amount of rain (AH 703).
    rainfall_to_max_30_SI = df['Cumulative rain depth (mm)'].max() * 2

    # if the maximum 30 min rainfall is not equal to 0:
    if df['30-Min Rainfall (mm)'].max() != 0:

        # finds the index of the row with the maximum value in the "30-Min Rainfall (mm)"
        max_row_SI = df['30-Min Rainfall (mm)'].idxmax()

        # then retrieves the value from the 'RAIN (mm)' column at that index
        rainfall_to_max_30_SI = df.at[max_row_SI, 'Cumulative rain depth (mm)']

        # calculate the maximum rainfall intensity with in 30 minutes
        max_30_min_rainfall_intensity_SI = rainfall_to_max_30_SI * 60 / 30

    # if the maximum 30-Min rainfall is = 0, return the default: the I_30 is twice the amount of rain
    else:
        max_30_min_rainfall_intensity_SI = rainfall_to_max_30_SI

    # calculate the total energy of a storm
    total_energy_SI = df['Energy in Interval (MJ/ha)'].sum()
    
    # calculate rainfall erosivity of a storm
    rainfall_erosivity_SI = total_energy_SI * max_30_min_rainfall_intensity_SI

    # Collect summary for each storm
    for station_id in df['STID'].unique():
        summary_data.append({
            "Storm File": os.path.basename(file_path),
            "Station ID": station_id,
            "TIME":Time,
            "Total Rainfall (mm)": Total_rainfall_mm,
            "Rainfall @ Max 30-Min (mm)": rainfall_to_max_30_SI,
            "Max 30-Min Intensity (mm/h)": max_30_min_rainfall_intensity_SI,
            "Total Energy (MJ/ha)": total_energy_SI,
            "Rainfall Erosivity ((MJ-mm)/(ha-hr))": rainfall_erosivity_SI,
            "Day": df['Day'].iloc[0],
            "Month": df['Month'].iloc[0],
            "Year": df['Year'].iloc[0],
        })

# Convert summary data to DataFrame and save for each station
summary_df = pd.DataFrame(summary_data)
unique_stations = summary_df['Station ID'].unique()

for station_id in unique_stations:
    station_summary = summary_df[summary_df['Station ID'] == station_id]
    output_file_path = os.path.join(path_rainfall_erosivity, f"{station_id.replace('/', '_')}.csv")
    station_summary.to_csv(output_file_path, index=False)
    # print(f"Saved erosivity data for station {station_id} to {output_file_path}")

### 1.3.3 Calculate Average Monthly Precipiation

In [55]:
import os
import glob
import pandas as pd

# Define input and output paths
path_rainfall_storm = os.path.join(os.getcwd(), "Single_Storm_29")  # Input folder for rainfall data
path_result = os.path.join(os.getcwd(), "Result")  # Output folder for results
os.makedirs(path_result, exist_ok=True)  # Create the output folder if it doesn't exist

# Find all CSV files in the specified directory (recursively)
csv_files = glob.glob(os.path.join(path_rainfall_storm, '**/*.csv'), recursive=True)

# Initialize a list to store cumulative rain depth with timestamps for each site
all_data = []

# Loop through all CSV files
for file in csv_files:
    try:
        # Read each CSV file
        df = pd.read_csv(file)
        
        # Extract the last row's value of "Cumulative rain depth (mm)" column
        last_row = df.iloc[-1]
        cumulative_rain = last_row["Cumulative rain depth (mm)"]
        timestamp = last_row["TIME"]  # Adjust column name if needed
        stid = last_row["STID"]  # Adjust column name if needed

        # Append the data to a list
        all_data.append({'STID': stid, 'Month': pd.to_datetime(timestamp).month, 'Rainfall': cumulative_rain})
    except Exception as e:
        print(f"Error processing file {file}: {e}")

# Create a DataFrame from the collected data
rainfall_df = pd.DataFrame(all_data)

# Group by 'STID' and 'Month' and sum the total monthly rainfall per site
monthly_totals = rainfall_df.groupby(['STID', 'Month'])['Rainfall'].sum().reset_index()

# Compute the average monthly rainfall per site over 29 years
monthly_totals['AvgRainfall'] = monthly_totals['Rainfall'] / 29

# Convert data into a pivot table with months as columns
rainfall_pivot = monthly_totals.pivot(index="STID", columns="Month", values="AvgRainfall").reset_index()

# Rename columns with month names
month_names = {
    1: 'Jan (mm)', 2: 'Feb (mm)', 3: 'Mar (mm)', 4: 'Apr (mm)', 5: 'May (mm)', 6: 'Jun (mm)',
    7: 'Jul (mm)', 8: 'Aug (mm)', 9: 'Sep (mm)', 10: 'Oct (mm)', 11: 'Nov (mm)', 12: 'Dec (mm)'
}
rainfall_pivot.rename(columns=month_names, inplace=True)

# Fill missing values with 0 (in case some months are missing for a site)
rainfall_pivot.fillna(0, inplace=True)

# Calculate the average annual rainfall for each site
rainfall_pivot["Average Annual Rainfall (mm)"] = rainfall_pivot.iloc[:, 1:].sum(axis=1)

# Save the result to CSV
output_file = os.path.join(path_result, "average_monthly_rainfall_per_site.csv")
rainfall_pivot.to_csv(output_file, index=False)

print(f"Average monthly and annual rainfall data per site has been saved to: {output_file}")


Average monthly and annual rainfall data per site has been saved to: e:\Erosion and Vulnerability Assessment\R_estimation_gauge\R_Computation\Result\average_monthly_rainfall_per_site.csv


In [51]:
import os
import glob
import pandas as pd
import calendar

# Output directory
path_result = os.path.join(os.getcwd(), "Result")
os.makedirs(path_result, exist_ok=True)

# Input directory
path_rainfall_erosivity = os.path.join(os.getcwd(), "Rainfall_erosivity_29")

# Find all CSV files in the Rainfall Erosivity folder
csv_files = glob.glob(os.path.join(path_rainfall_erosivity, '*.csv'), recursive=True)

# Generate a list of month abbreviations (Jan, Feb, ..., Dec)
month_names = [calendar.month_abbr[i] for i in range(1, 13)]

# Initialize a list to hold data for each station
station_results = []

for file in csv_files:
    # Extract station name from the filename
    station_name = os.path.basename(file).replace('.csv', '')
    
    # Read the current file
    data = pd.read_csv(file)

    # Define the long-term period
    Period = 29  

    # Calculate annual R factor and precipitation 
    annual_r_factor = data['Rainfall Erosivity ((MJ-mm)/(ha-hr))'].sum() / Period
    annual_P_mm = data['Total Rainfall (mm)'].sum() / Period

    # Calculate annual rainfall erosivity density
    annual_density = (
        annual_r_factor / annual_P_mm if annual_P_mm > 0 else 0
    )
    
    # Initialize dictionaries for monthly calculations
    monthly_r_factors = {}
    
    monthly_P_mm = {}
    monthly_contributions = {}
    monthly_erosivity_density = {}
    
    for month_idx, month_name in enumerate(month_names):
        # Filter data for the current month
        monthly_data = data[data['Month'] == month_idx+1]
        
        # Monthly sums
        monthly_r_sum = monthly_data['Rainfall Erosivity ((MJ-mm)/(ha-hr))'].sum()

        monthly_P_mm_sum = monthly_data['Total Rainfall (mm)'].sum()
        
        # Calculate monthly R factor, precipitation, and contributions
        monthly_r_factors[f'{month_name} R'] = monthly_r_sum / Period
   
        monthly_P_mm[f'{month_name} P(mm)'] = monthly_P_mm_sum / Period
        monthly_contributions[f'{month_name} R contribution (%)'] = (
            (monthly_r_sum / (Period * annual_r_factor) * 100) if annual_r_factor > 0 else 0
        )
        
        # Calculate monthly rainfall erosivity density
        monthly_erosivity_density[f'{month_name} R Density ((MJ-mm)/(ha-hr-mm))'] = (
            monthly_r_sum / monthly_P_mm_sum if monthly_P_mm_sum > 0 else 0
        )
    
    # Create a dictionary for the station with all calculated values
    station_results.append({
        'stid': station_name, 
        'Period (Years)': Period,
        'Annual R Factor': annual_r_factor, 
    
        'Annual P (mm)': annual_P_mm,
      

        **monthly_P_mm,
        **monthly_contributions,
        **monthly_erosivity_density
    })

# Convert the list of dictionaries to a DataFrame
station_results_df = pd.DataFrame(station_results)

# Save the station-level results to a CSV file
station_results_df.to_csv(os.path.join(path_result, 'R_factor_results.csv'), index=False)

# Initialize a list for state results and calculate the average monthly R factor, contributions, and densities
state_results = []
state_density_results = []

for month_name in month_names:
    # State-level averages
    avg_r = station_results_df[f'{month_name} R'].mean()
    avg_contribution = station_results_df[f'{month_name} R contribution (%)'].mean()
    avg_density = station_results_df[f'{month_name} R Density ((MJ-mm)/(ha-hr-mm))'].mean()
    
    state_results.append({
        'Month': month_name, 
        'Monthly R Average': avg_r,
        'Mean Contribution (%)': avg_contribution
    })
    
    state_density_results.append({
        'Month': month_name,
        'Mean R Density ((MJ-mm)/(ha-hr-mm))': avg_density
    })





# Convert the state results lists to DataFrames
state_results_df = pd.DataFrame(state_results)
state_density_df = pd.DataFrame(state_density_results)

# Save the state results to CSV files
state_results_df.to_csv(os.path.join(path_result, 'state_monthly_R_averages.csv'), index=False)
state_density_df.to_csv(os.path.join(path_result, 'state_monthly_R_density_averages.csv'), index=False)

print("Processing complete. Results saved to:", path_result)


KeyError: 'Jan R'

# 2 Save the Calculated R to Mesonet Station file

Operation this code require to: 
Installing arcpy package to work with jupyter notebook (The installation instraction step by step can be learnt from https://www.youtube.com/watch?v=DmqtYJ-liKU).

In Part II have obtained results including long term average annual R factor, monthly R factor, and monthly contribution to annaul R factor for each site where recording precipiation over 10 years. However, those data are saved in "R_factor_results.**csv**" file. For geo-processing, this section save those data in **existed shapefile (named as "ok_mesonet_sites_all_20210715.shp")** recorded general information like station ID, station name, station coordinates, and elevation, etc., produced by Mesonet (https://mesonet.org/index.php/site/sites/mesonet_sites). 

This cell is using **AddJoin Tool** (https://pro.arcgis.com/en/pro-app/latest/tool-reference/data-management/add-join.htm) to save the calculated results in .csv into shapefile based on a common field, "stid", in this case. JoinField Tool also can join a layer to another layer or table based on a common field. However, the JoinField Tool will join a layer permanently, which can change the original shapefile. The original shapefile is not expected to be change, so that AddJoin Tool is applied in this case since the this tool joins a layer temporarily. According to copy the temporary layer, the joined layer can be saved as a permanet layer without changing the original layer.  

In [12]:


# Path to your ZIP file
zip_file_path = os.path.join(os.getcwd(), "mesonet_sites_shape.zip")
# zip_file_path = os.path.join(base_dir,"Geoprocess_inputs" ,"mesonet_sites_shape.zip")

# Destination directory where the contents of the zip will be extracted
extract_to_directory =os.path.join(os.getcwd(),"Geoprocess_inputs")

# Ensure the destination directory exists
os.makedirs(extract_to_directory, exist_ok=True)

# Extract the ZIP file
with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
    zip_ref.extractall(extract_to_directory)

# Paths to the shapefile and the join table CSV
shapefile_path = os.path.join(os.getcwd(),"Geoprocess_inputs", "mesonet_sites_shape","ok_mesonet_sites_all_20210715.shp")
join_table = os.path.join(os.getcwd(), "Result_29", "R_factor_results.csv")
output_dir = os.path.join(os.getcwd(), "shapefile_outputs")

# Ensure the output directory exists
os.makedirs(output_dir, exist_ok=True)

arcpy.env.workspace = output_dir
arcpy.env.overwriteOutput = True

# The qualifiedFieldNames environment is used by Copy Features when persisting the join field names.
arcpy.env.qualifiedFieldNames = False


# Process: Create a Feature Layer from the shapefile
temp_layer_sites = "mesonet_sites_layer"
arcpy.MakeFeatureLayer_management(shapefile_path, temp_layer_sites)
print("Temporary layer created.")

# Process: Add Join
joined_table_temp_layer = arcpy.management.AddJoin(temp_layer_sites, "stid", join_table, "stid")
print("JoinField operation completed.")

# Process: Copy Features to new shapefile
joined_shapefile_path = os.path.join(output_dir, "MesoSite_R.shp")
arcpy.CopyFeatures_management(joined_table_temp_layer, joined_shapefile_path)
print("New shapefile with joined data created.")

# Process: List and print field names in the new shapefile
fields = arcpy.ListFields(joined_shapefile_path)
for field in fields:
    print(field.name)

# Process: Remove records where Annual R Factor = 0
with arcpy.da.UpdateCursor(joined_shapefile_path, ['Annual_R_F']) as cursor:
    for row in cursor:
        if row[0] == 0:
            cursor.deleteRow()
print("Records with R factor = 0 removed.")



Temporary layer created.
JoinField operation completed.
New shapefile with joined data created.
FID
Shape
stnm
stid
name
city
rang
cdir
cnty
nlat
elon
elev
cdiv
clas
WCR05
WCS05
A05
N05
BULK5
GRAV5
SAND5
SILT5
CLAY5
TEXT5
WCR10
WCS10
A10
N10
WCR25
WCS25
A25
N25
BULK25
GRAV25
SAND25
SILT25
CLAY25
TEXT25
WCR60
WCS60
A60
N60
BULK60
GRAV60
SAND60
SILT60
CLAY60
TEXT60
WCR75
WCS75
A75
N75
BULK75
GRAV75
SAND75
SILT75
CLAY75
TEXT75
datc
datd
stid_1
Period__Ye
Annual_R_F
Annual_P__
Annual_P_1
Annual_R_D
Jan_R
Feb_R
Mar_R
Apr_R
May_R
Jun_R
Jul_R
Aug_R
Sep_R
Oct_R
Nov_R
Dec_R
Jan_P_in_
Feb_P_in_
Mar_P_in_
Apr_P_in_
May_P_in_
Jun_P_in_
Jul_P_in_
Aug_P_in_
Sep_P_in_
Oct_P_in_
Nov_P_in_
Dec_P_in_
Jan_P_mm_
Feb_P_mm_
Mar_P_mm_
Apr_P_mm_
May_P_mm_
Jun_P_mm_
Jul_P_mm_
Aug_P_mm_
Sep_P_mm_
Oct_P_mm_
Nov_P_mm_
Dec_P_mm_
Jan_R_cont
Feb_R_cont
Mar_R_cont
Apr_R_cont
May_R_cont
Jun_R_cont
Jul_R_cont
Aug_R_cont
Sep_R_cont
Oct_R_cont
Nov_R_cont
Dec_R_cont
Jan_R_Dens
Feb_R_Dens
Mar_R_Dens
Apr_R_Dens
May_R_Dens
J